In [ ]:
import numpy as np
import matplotlib.pylab as plt
import os,time
from astropy.nddata import CCDData
from astropy import wcs
from astropy.io import fits
import ccdproc

In [ ]:
def imlist(fname,ext='.fits'):
    # ensures all files have requested extension
    imnames=open(fname,'r').readlines()
    imnames=[s.replace('\n','') for s in imnames]    
    imnames=[s.replace(ext,'') for s in imnames]
    imnames=[s+ext for s in imnames]
    return imnames

### ENTER DATA DIRECTORY

In [ ]:
band = 'V'
datadir = '/home/astrotech1/Desktop/M101/'+band+'data'

os.chdir(datadir)

### GENERATE A REFERENCE TO REGISTER EACH IMAGE TO

In [ ]:
def genref():
    # set up the reference image
    
    NX,NY = 4000,4000 # make a 4000,4000 pixel image
    cdelt = 1.45/3600. # give it the Schmidt pixel scale of 1.45 arcsec/pix
    RA0,Dec0 = 210.75708333333, 54.3498611111112  # center coordinate is M101's center
    
    hdu_ref=fits.PrimaryHDU(np.zeros((NX,NY),dtype=np.float32))
    w = wcs.WCS(naxis=2)
    w.wcs.crpix = [0.5*NX, 0.5*NY]
    w.wcs.cdelt = np.array([-cdelt,cdelt])
    w.wcs.crval = [RA0,Dec0]
    w.wcs.ctype = ["RA---TAN", "DEC--TAN"]
    hdr_wcs=w.to_header()
    hdu_ref.header.update(hdr_wcs)
    refhdr=hdu_ref.header
    return refhdr

### READ IN ALL THE IMAGES, PLUS THEIR PHOTOMETRIC ZEROPOINTS AND COLOR TERMS

In [ ]:
imnames=imlist('images.lis')
imnames=['cr'+s for s in imnames]

image_zp=[]
image_cterm=[]
images=[]
print('Reading images and collating ZPs...')
for imname in imnames:
    
    print('   Working on {}'.format(imname))
    image=CCDData.read(imname)
    
    image_zp.append(image.header['ZPOINT'])
    image_cterm.append(image.header['CTERM'])
    images.append(image)

### CALCULATE AVERAGE ZEROPOINT AND COLOR TERM, PLUS ZEROPOINT SCALING FACTOR FOR EACH IMAGE

In [ ]:
combine_zp=np.average(image_zp)
combine_cterm=np.average(image_cterm)
print('Average ZP , CTERM = {:.3f} , {:.3f}'.format(combine_zp,combine_cterm))
scale_fac=10**(0.4*(image_zp-combine_zp))

PhotFig=plt.figure(figsize=(8,4))
ZPplot=PhotFig.add_subplot(121)
ZPplot.hist(image_zp)
ZPplot.set_xlabel('ZP')
Cplot=PhotFig.add_subplot(122)
Cplot.hist(image_cterm)
Cplot.set_xlabel('CTERM')

### FOR EACH IMAGE, REGISTER TO REFERENCE IMAGE AND SCALE TO AVERAGE ZEROPOINT
### THEN MEDIAN COMBINE THE REGISTERED IMAGES TOGETHER

In [ ]:
print('Registering images...')
st=time.time()

reprojected=[]
for image,scale in zip(images,scale_fac):

    newhdr=genref()
    newim=ccdproc.wcs_project(image,wcs.WCS(newhdr),
                              target_shape=(newhdr['NAXIS1'],newhdr['NAXIS2']))
    newim.data *= scale
    reprojected.append(newim)

    
print('Combining images...')
combiner = ccdproc.Combiner(reprojected)
combined = combiner.median_combine()
combined.header=newhdr
combined.header['ZPOINT']=combine_zp
combined.header['CTERM']=combine_cterm
outfile = 'M101_'+band+'stack.fits'
combined.write(outfile,overwrite=True)

et=time.time()
print('Calibrating: {:.1f} sec'.format(et-st))
print('Finished!')